<a href="https://colab.research.google.com/github/s-u-s-h-ii/rakha_mines/blob/main/SubSurface_V4_Aayush.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
%pip install trimesh manifold3d

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 740.3/740.3 kB 35.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.2/1.2 MB 60.3 MB/s eta 0:00:00


In [ ]:
import numpy as np
import pandas as pd
import plotly.graph_objects as go
from scipy.spatial import Delaunay, cKDTree
from sklearn.neighbors import NearestNeighbors
from collections import defaultdict
import trimesh
np.set_printoptions(suppress=True)
from tqdm import tqdm

# ============================================================
# PARAMETERS (UNCHANGED)
# ============================================================
K_NEIGHBORS = 4
ALPHA = 350.0
BARREN_RADIUS = 1.0
BUFFER_DIST = 5.0
BARREN_MARGIN = 5.0
MIN_ZONE_POINTS = 4

# ============================================================
# LOAD NEW DATA
# ============================================================
bore = pd.read_csv("/content/drive/MyDrive/Minzari Data Personal Copy/Data_08012026/Borehole_no_mag.csv")
lode = pd.read_csv("/content/drive/MyDrive/Minzari Data Personal Copy/Data_08012026/lodes_cutoff_0.5 (2).csv")

# expected columns
# Borehole: BHID, X, Y, Z, DEPTH, OREZONE
# Lode: BHID, FROM, TO, THICKNESS, AVG_OREZONE

In [ ]:
bore["OREZONE_BINARY"].value_counts()

OREZONE_BINARY
0    91157
1    23509
Name: count, dtype: int64

In [ ]:
lode

BHID   FROM      TO  THICKNESS  AVG_OREZONE  CUTOFF_OREZONE
0   MHCM06  187.9  192.80       4.90     1.200000             0.5
1   MHCM15  241.0  259.00      18.00     0.600000             0.5
2   MNJ001  240.3  242.30       2.00     1.506250             0.5
3   MNJ001  261.5  265.95       4.45     1.328494             0.5
4   MNJ001  292.8  293.80       1.00     1.051500             0.5
5   MNJ002  215.9  218.90       3.00     0.536667             0.5
6   MNJ002  219.9  221.40       1.50     0.614333             0.5
7   MNJ002  230.4  238.40       8.00     0.801000             0.5
8   MNJ003  308.9  313.40       4.50     0.562556             0.5
9   MNJ004  102.0  104.00       2.00     1.869500             0.5
10  MNJ004  350.0  352.30       2.30     0.830913             0.5
11  MNJ004  379.8  402.30      22.50     0.500467             0.5
12  MNJ005  103.4  104.90       1.50     0.505000             0.5
13  MNJ006  218.3  221.30       3.00     0.501500             0.5
14  MNJ006  237.3  239.30       2.00     0.646500             0.5
15  MNJ008  193.3  199.30       6.00     0.576667             0.5
16  MNJ008  231.8  234.30       2.50     2.003800             0.5
17  MNJ008  247.8  249.30       1.50     0.510000             0.5
18  MNJ009  318.3  324.80       6.50     0.778615             0.5
19  MNJ009  391.3  392.30       1.00     0.622500             0.5
20  MNJ010  164.8  173.30       8.50     0.759941             0.5
21  MNJ010  188.8  190.30       1.50     0.683000             0.5
22  MNJ011  199.3  200.30       1.00     0.745000             0.5
23  MNJ011  233.8  234.80       1.00     0.884000             0.5
24  MNJ011  259.8  263.60       3.80     0.729605             0.5
25  MNJ012   79.8   80.80       1.00     0.600000             0.5
26  MNJ012  260.5  264.70       4.20     1.225476             0.5
27  MNJ012  370.8  372.80       2.00     0.977500             0.5
28  MNJ012  394.8  396.90       2.10     0.521429             0.5
29  MNJ013  428.3  429.30       1.00     0.560000             0.5
30  MNJ015  453.8  456.30       2.50     0.504954             0.5
31  MNJ016  270.3  271.30       1.00     0.509500             0.5
32  MNJ016  316.3  318.80       2.50     0.556000             0.5
33  MNJ016  457.3  458.80       1.50     1.172000             0.5
34  MNJ017  136.8  137.80       1.00     0.904850             0.5
35  MNJ018   79.8   80.80       1.00     0.603147             0.5
36  MNJ018  260.5  264.70       4.20     1.225128             0.5
37  MNJ018  370.8  372.80       2.00     0.977859             0.5
38  MNJ018  394.8  396.90       2.10     0.520426             0.5
39  MNJ021  129.3  132.30       3.00     1.612267             0.5
40  MNJ021  367.8  368.80       1.00     1.062950             0.5

In [ ]:
d.simplices

array([[30, 11,  7, 12],
       [30,  5,  7, 12],
       [30,  5, 23,  7],
       [30,  5, 33, 12],
       [29, 30, 23,  7],
       [29, 30, 11,  7],
       [29, 30, 11, 12],
       [22, 29, 23,  7],
       [21,  5,  4,  7],
       [21,  5, 23,  7],
       [21, 22,  6, 23],
       [25, 21,  6,  4],
       [13,  1,  4,  7],
       [27, 22,  7,  0],
       [27, 22, 29,  7],
       [27, 22, 29, 23],
       [27, 22, 20, 23],
       [27, 20,  5, 23],
       [16, 21, 23,  7],
       [16, 21,  6, 23],
       [16, 13,  4,  7],
       [18, 20,  5, 23],
       [18, 21,  5, 23],
       [18, 21,  5,  4],
       [18,  5,  4, 12],
       [18,  5, 33, 12],
       [19, 22, 20, 23],
       [19, 18, 20, 23],
       [19, 18, 21, 23],
       [19, 18, 21,  4],
       [19, 18, 33,  4],
       [24, 13,  1,  4],
       [31, 29,  7,  0],
       [31, 27,  7,  0],
       [31, 27, 29,  7],
       [32, 31, 30, 33],
       [32, 30, 33, 12],
       [32, 29, 30, 12],
       [34, 29, 30, 23],
       [34, 27, 29, 23],


In [ ]:
# def alpha_shape_3d(pts, alpha):
d = Delaunay(P)
faces = defaultdict(int)

for tet in d.simplices:
    v = P[tet]
    c = v.mean(axis=0)
    if np.max(np.linalg.norm(v - c, axis=1)) <= ALPHA:
        for i in range(4):
            f = tuple(sorted(tet[np.arange(4) != i]))
            print(f)
            faces[f] += 1
    print()
# return np.array([f for f, c in faces.items() if c == 1])




(np.int32(5), np.int32(12), np.int32(33))
(np.int32(12), np.int32(30), np.int32(33))
(np.int32(5), np.int32(12), np.int32(30))
(np.int32(5), np.int32(30), np.int32(33))



(np.int32(11), np.int32(12), np.int32(30))
(np.int32(11), np.int32(12), np.int32(29))
(np.int32(12), np.int32(29), np.int32(30))
(np.int32(11), np.int32(29), np.int32(30))




(np.int32(6), np.int32(22), np.int32(23))
(np.int32(6), np.int32(21), np.int32(23))
(np.int32(21), np.int32(22), np.int32(23))
(np.int32(6), np.int32(21), np.int32(22))

(np.int32(4), np.int32(6), np.int32(21))
(np.int32(4), np.int32(6), np.int32(25))
(np.int32(4), np.int32(21), np.int32(25))
(np.int32(6), np.int32(21), np.int32(25))





(np.int32(20), np.int32(22), np.int32(23))
(np.int32(20), np.int32(23), np.int32(27))
(np.int32(22), np.int32(23), np.int32(27))
(np.int32(20), np.int32(22), np.int32(27))

(np.int32(5), np.int32(20), np.int32(23))
(np.int32(5), np.int32(23), np.int32(27))
(np.int32(20), np.int32(23), np.int32(27))
(np.int3

In [ ]:
d

In [ ]:
# ============================================================
# ALPHA SHAPE FUNCTIONS (UNCHANGED)
# ============================================================
def alpha_shape_3d(pts, alpha):
    d = Delaunay(pts)
    faces = defaultdict(int)

    for tet in d.simplices:
        v = pts[tet]
        c = v.mean(axis=0)
        if np.max(np.linalg.norm(v - c, axis=1)) <= alpha:
            for i in range(4):
                f = tuple(sorted(tet[np.arange(4) != i]))
                faces[f] += 1

    return np.array([f for f, c in faces.items() if c == 1])

def mesh_volume(V, F):
    return abs(sum(
        np.dot(V[f[0]], np.cross(V[f[1]], V[f[2]]))
        for f in F
    )) / 6.0

In [ ]:
# ============================================================
# BUILD LODE INTERVAL LOOKUP
# ============================================================
lode_map = defaultdict(list)
for _, r in lode.iterrows():
    lode_map[r.BHID].append((r.FROM, r.TO, r.AVG_OREZONE))

# ============================================================
# ASSIGN HIGH / NON ORE USING FROM–TO
# ============================================================
ore_rows = []
non_ore_rows = []
ore_bhids = set()
non_ore_bhids = {}

for _, r in bore.iterrows():
    bhid = r.BHID
    depth = r.DEPTH

    matched = False
    avg_val = None

    for f, t, avg in lode_map.get(bhid, []):
        if f <= depth <= t:
            matched = True
            avg_val = avg
            break

    if matched:
        ore_rows.append([
            r.X, r.Y, r.Z, r.BHID, r.OREZONE, avg_val
        ])
        ore_bhids.add(r.BHID)
    else:
        non_ore_rows.append([r.X, r.Y, r.Z])
        if r.BHID in non_ore_bhids.keys():
          non_ore_bhids[r.BHID].append([r.X, r.Y, r.Z])
        else:
          non_ore_bhids[r.BHID] = [[r.X, r.Y, r.Z]]

ore_df = pd.DataFrame(
    ore_rows,
    columns=["X", "Y", "Z", "BHID", "OREZONE", "AVG_OREZONE"]
)

non_ore_pts = np.array(non_ore_rows)

print(f"High-grade points: {len(ore_df)}")
print(f"Non-ore points: {len(non_ore_pts)}")

# ============================================================
# NON-ORE KD TREE (UNCHANGED)
# ============================================================
non_ore_tree = cKDTree(non_ore_pts) if len(non_ore_pts) else None

# ============================================================
# ZONE CLUSTERING (UNCHANGED IDEA)
# ============================================================
stats = (
    ore_df
    .groupby("BHID")
    .agg(
        X=("X","mean"),
        Y=("Y","mean"),
        Z=("Z","mean"),
        n=("X","count")
    )
    .reset_index()
)

stats = stats[stats.n >= MIN_ZONE_POINTS]
coords = stats[['X','Y','Z']].values

# ============================================================
# KNN CONNECTIVITY
# ============================================================
nbrs = NearestNeighbors(n_neighbors=K_NEIGHBORS+1).fit(coords)
_, idx = nbrs.kneighbors(coords)

graph = defaultdict(set)
for i, n in enumerate(idx):
    for j in n[1:]:
        graph[i].add(j)
        graph[j].add(i)

visited = set()
components = []

for i in range(len(coords)):
    if i in visited:
        continue
    stack = [i]
    comp = set()
    while stack:
        n = stack.pop()
        if n in visited:
            continue
        visited.add(n)
        comp.add(n)
        stack += graph[n] - visited
    components.append(comp)

High-grade points: 1500
Non-ore points: 113166


In [ ]:
components

[{0,
  1,
  2,
  3,
  4,
  np.int64(5),
  6,
  np.int64(7),
  np.int64(8),
  9,
  np.int64(10),
  11,
  np.int64(12),
  13,
  14,
  np.int64(15),
  16,
  17,
  18}]

In [ ]:
(
    ore_df
    .groupby("BHID")
    .agg(
        X=("X","mean"),
        Y=("Y","mean"),
        Z=("Z","mean"),
        n=("X","count")
    )
    .reset_index()
)

BHID              X             Y           Z    n
0   MHCM06  352829.805045  2.248376e+06   86.853083   50
1   MHCM15  352811.349695  2.248376e+06   41.559305  181
2   MNJ001  352822.289773  2.248388e+06   26.337941   77
3   MNJ002  352771.563414  2.247922e+06   37.451245  128
4   MNJ003  352742.177370  2.247932e+06  -26.852382   46
5   MNJ004  352784.209714  2.248388e+06  -63.090327  270
6   MNJ005  352680.902742  2.247602e+06  141.234815   16
7   MNJ006  352691.508853  2.247411e+06   48.646670   52
8   MNJ008  352669.509168  2.247338e+06   54.211524  103
9   MNJ009  352654.281244  2.247412e+06  -48.777038   77
10  MNJ010  352654.633517  2.247213e+06   79.683024  102
11  MNJ011  352629.517128  2.247120e+06    8.582034   61
12  MNJ012  352759.713712  2.248474e+06   -5.709622   97
13  MNJ013  352690.126584  2.249566e+06 -124.117450   11
14  MNJ015  352685.945728  2.248031e+06 -198.287448   26
15  MNJ016  352594.725795  2.247621e+06  -78.993024   53
16  MNJ017  352328.475544  2.247052e+06  107.146097   11
17  MNJ018  352735.455013  2.248167e+06  -15.035824   97
18  MNJ021  352691.834735  2.248672e+06   69.168625   42

In [ ]:
# # ============================================================
# # BUILD BARREN ENVELOPES
# # ============================================================
# barren_meshes = []

# for bhid in list(set(non_ore_bhids) - ore_bhids):
#   pts = non_ore_bhids[bhid]
#   start = pts[0]
#   end   = pts[-1]

#   cap = trimesh.creation.cylinder(
#       radius=BARREN_RADIUS,
#       segment=[start, end]
#   )
#   barren_meshes.append(cap)

# for bhid in tqdm(list(ore_bhids)):
#     pts = non_ore_bhids[bhid]
#     for i in range(len(pts)-1):
#         cap = trimesh.creation.cylinder(
#             radius=BARREN_RADIUS,
#             segment=[pts[i], pts[i+1]]
#         )
#         barren_meshes.append(cap)

# barren_union = trimesh.util.concatenate(barren_meshes)

In [ ]:
components[0]

{0,
 1,
 2,
 3,
 4,
 np.int64(5),
 6,
 np.int64(7),
 np.int64(8),
 9,
 np.int64(10),
 11,
 np.int64(12),
 13,
 14,
 np.int64(15),
 16,
 17,
 18}

In [ ]:
coords[list(components[0])]

array([[ 352829.80504481, 2248376.        ,      86.85308284],
       [ 352811.3496953 , 2248376.142     ,      41.5593047 ],
       [ 352822.28977305, 2248387.80751425,      26.33794092],
       [ 352771.56341416, 2247921.7375731 ,      37.45124453],
       [ 352742.17737019, 2247931.75884723,     -26.85238205],
       [ 352784.20971443, 2248388.253936  ,     -63.09032744],
       [ 352680.90274157, 2247602.08431974,     141.23481519],
       [ 352691.50885281, 2247411.02259831,      48.64666991],
       [ 352669.50916848, 2247338.09503573,      54.2115244 ],
       [ 352654.28124412, 2247411.58769839,     -48.77703823],
       [ 352654.63351725, 2247212.54810431,      79.68302382],
       [ 352629.51712806, 2247119.99119552,       8.58203359],
       [ 352759.7137115 , 2248473.80813859,      -5.70962233],
       [ 352690.12658375, 2249566.45413446,    -124.11745027],
       [ 352685.94572813, 2248031.02867111,    -198.28744761],
       [ 352594.72579546, 2247620.62430965,     -78.993

In [ ]:
F

TrackedArray([[ 0,  0,  9],
              [ 1,  7, 13],
              [ 1,  3,  7],
              [ 1,  3, 10],
              [ 1,  8, 10],
              [ 0,  9, 10],
              [ 0,  8, 10],
              [ 0,  0, 17],
              [ 0,  0, 22],
              [ 0,  0, 17],
              [ 7,  9, 10],
              [ 3,  7, 10],
              [ 0,  7,  9],
              [ 7, 13, 16],
              [ 0,  0, 22],
              [ 0,  0, 27],
              [ 0, 17, 25],
              [ 0, 24, 25],
              [ 0,  1, 24],
              [ 1,  4, 13],
              [ 1,  4, 24],
              [ 4, 24, 26],
              [24, 25, 26],
              [28, 32, 33],
              [ 0, 28, 32],
              [ 0,  0, 27],
              [ 0,  0, 28],
              [ 0, 19, 33],
              [19, 28, 33],
              [ 0,  4, 18],
              [ 0,  4, 19],
              [ 0, 22, 23],
              [ 0,  0, 33],
              [ 5, 12, 30],
              [ 0,  0, 18],
              [ 0, 1

In [ ]:
# ============================================================
# BUILD ENVELOPES
# ============================================================
hulls = []
total_volume = 0.0
all_points = []

print("Starting envelope")
for comp in tqdm(components):
    P = coords[list(comp)]
    if len(P) < 4:
        continue

    F = alpha_shape_3d(P, ALPHA)
    if len(F) == 0:
        continue

    buf = []
    for f in F:
        tri = P[f]
        cen = tri.mean(axis=0)
        n = np.cross(tri[1]-tri[0], tri[2]-tri[0])
        if np.linalg.norm(n) < 1e-6:
            continue
        n /= np.linalg.norm(n)

        for s in (+1, -1):
            p = cen + s * BUFFER_DIST * n
            if non_ore_tree:
                d, _ = non_ore_tree.query(p, distance_upper_bound=BARREN_MARGIN)
                if not np.isinf(d):
                    continue
            buf.append(p)

    if not buf:
        continue

    allp = np.vstack([P, np.array(buf)])
    F2 = alpha_shape_3d(allp, ALPHA)
    if len(F2) == 0:
        continue

    mesh = trimesh.Trimesh(vertices=allp, faces=F2, process=True)
    # mesh = mesh.process(validate=True)
    # ========================================================
    # THE FIX: VERTEX PRUNING (Instead of Boolean)
    # ========================================================
    if non_ore_tree:
        # Check every vertex of the new mesh
        # If it is too close to a barren point, mark it for deletion
        # effectively "cutting" the barren cylinder out of the mesh
        vertex_dists, _ = non_ore_tree.query(mesh.vertices)
        # Identify vertices to KEEP (distance > radius)
        mask_keep = vertex_dists > BARREN_RADIUS
        # If we are removing vertices, we must update the mesh
        if not np.all(mask_keep):
            mesh.update_vertices(mask_keep)
            mesh.remove_unreferenced_vertices()

    vol = mesh_volume(mesh.vertices, mesh.faces)
    total_volume += vol
    hulls.append((mesh.vertices, mesh.faces, vol))
    # vol = mesh_volume(allp, F2)
    # total_volume += vol
    # hulls.append((allp, F2, vol))

Starting envelope


100%|██████████| 1/1 [00:00<00:00, 10.63it/s]


In [ ]:
# ============================================================
# VISUALIZATION
# ============================================================
fig = go.Figure()
# --- NON-ORE POINTS ---
fig.add_trace(go.Scatter3d(
    x=non_ore_pts[:,0],
    y=non_ore_pts[:,1],
    z=non_ore_pts[:,2],
    mode='markers',
    marker=dict(size=2, color='grey'),
    name="Non-Ore"
))

# --- ORE POINTS ---
fig.add_trace(go.Scatter3d(
    x=ore_df.X,
    y=ore_df.Y,
    z=ore_df.Z,
    mode='markers',
    marker=dict(
        size=4,
        color=ore_df.AVG_OREZONE,
        colorscale='Viridis',
        colorbar=dict(title="AVG_OREZONE")
    ),
    hovertemplate=
        "BHID: %{customdata[0]}<br>"
        "OREZONE: %{customdata[1]}<br>"
        "AVG_OREZONE: %{marker.color}<extra></extra>",
    customdata=np.c_[ore_df.BHID, ore_df.OREZONE],
    name="Ore Points"
))

# --- ENVELOPES ---
for i, (P, F, V) in enumerate(hulls):
    fig.add_trace(go.Mesh3d(
        x=P[:,0], y=P[:,1], z=P[:,2],
        i=F[:,0], j=F[:,1], k=F[:,2],
        opacity=0.45,
        color='orange',
        name=f"Envelope {i+1}"
    ))

fig.update_layout(
    title=f"Ore / Non-Ore Model | Total Volume = {(total_volume*2800*0.005)/1e9:.2f} million tonnes",
    scene=dict(aspectmode='data'),
    margin=dict(l=0, r=0, t=40, b=0)
)

fig.show()

In [ ]:
total_volume

np.float64(11413603572.617891)

In [ ]:
#!/usr/bin/env python3
"""
Ore Body Visualization - 100% REAL DATA ONLY
Planes (Inferred Lodes) are STRICTLY within ore zones only.NO dummy/synthetic data used."""

import numpy as np
import pandas as pd
from scipy.spatial import ConvexHull, Delaunay, cKDTree
from scipy.interpolate import griddata
from sklearn.decomposition import PCA
import plotly.graph_objects as go
import warnings
warnings.filterwarnings('ignore')

# =============================================================================
# 1.DATA LOADING - 100% REAL DATA
# =============================================================================

def load_collar_data(filepath):
    df = pd.read_csv(filepath)
    df.columns = df.columns.str.strip()
    print(f"  Loaded {len(df)} collars from {filepath}")
    return df

def load_survey_data(filepath):
    df = pd.read_csv(filepath)
    df.columns = df.columns.str.strip()
    print(f"  Loaded {len(df)} survey records from {filepath}")
    return df

def load_assay_data(filepath):
    df = pd.read_csv(filepath)
    df.columns = df.columns.str.strip()
    df['BHID'] = df['BHID'].apply(standardize_bhid)
    print(f"  Loaded {len(df)} assay intervals from {filepath}")
    return df

def standardize_bhid(bhid):
    bhid = str(bhid).strip()
    if bhid.startswith('MNJ') and len(bhid) == 5:
        return f"MNJ0{bhid[3:]}"
    return bhid

# =============================================================================
# 2.CONTROLS
# =============================================================================

CONTROLS = {
    "cutoff_grade": 0.2,
    "surface_padding": 50,
    "mesh_resolution": 40,
    "samples_per_meter": 0.5,
    "alpha": 100.0,
    "cluster_eps": 120.0,
    "min_cluster_pts": 4,
    "barren_margin": 15.0,
    "strict_ore_only": True,
}

# =============================================================================
# 3.BOREHOLE DESURVEY - REAL DATA
# =============================================================================

def desurvey_borehole(collar_row, survey_df, max_depth, samples_per_meter=0.5):
    bhid = collar_row['BHID']
    collar_x = collar_row['XCOLLAR']
    collar_y = collar_row['YCOLLAR']
    collar_z = collar_row['ZCOLLAR']

    surveys = survey_df[survey_df['BHID'] == bhid].sort_values('AT').copy()

    if len(surveys) == 0:
        surveys = pd.DataFrame({
            'BHID': [bhid, bhid],
            'AT': [0, max_depth],
            'BRG': [0, 0],
            'DIP': [90, 90]
        })

    n_points = max(int(max_depth * samples_per_meter), 10)
    depths = np.linspace(0, max_depth, n_points)

    points = []
    curr_x, curr_y, curr_z = collar_x, collar_y, collar_z
    prev_depth = 0

    survey_depths = surveys['AT'].values
    survey_azi = surveys['BRG'].values
    survey_dip = surveys['DIP'].values

    prev_azi = np.radians(survey_azi[0])
    prev_dip = np.radians(survey_dip[0])

    for depth in depths:
        azi = np.radians(np.interp(depth, survey_depths, survey_azi))
        dip = np.radians(np.interp(depth, survey_depths, survey_dip))

        if depth > 0:
            delta_depth = depth - prev_depth

            dx1 = np.sin(prev_azi) * np.cos(prev_dip)
            dy1 = np.cos(prev_azi) * np.cos(prev_dip)
            dz1 = -np.sin(prev_dip)

            dx2 = np.sin(azi) * np.cos(dip)
            dy2 = np.cos(azi) * np.cos(dip)
            dz2 = -np.sin(dip)

            cos_theta = np.clip(dx1*dx2 + dy1*dy2 + dz1*dz2, -1, 1)
            theta = np.arccos(cos_theta)
            rf = 2 / theta * np.tan(theta / 2) if theta > 0.0001 else 1

            curr_x += delta_depth / 2 * (dx1 + dx2) * rf
            curr_y += delta_depth / 2 * (dy1 + dy2) * rf
            curr_z += delta_depth / 2 * (dz1 + dz2) * rf

        points.append([curr_x, curr_y, curr_z, depth])
        prev_depth = depth
        prev_azi = azi
        prev_dip = dip

    return np.array(points)

# =============================================================================
# 4.GRADE ASSIGNMENT - REAL DATA
# =============================================================================

def assign_grades_to_trace(trace, bhid, assay_df, cutoff=0.2):
    n_points = len(trace)
    grades = np.zeros(n_points)
    mineral_flags = np.zeros(n_points, dtype=int)

    hole_assays = assay_df[assay_df['BHID'] == bhid]

    for i, point in enumerate(trace):
        depth = point[3]
        mask = (hole_assays['FROM'] <= depth) & (hole_assays['TO'] > depth)
        matching = hole_assays[mask]

        if len(matching) > 0:
            grade = matching.iloc[0]['Cu%']
            grades[i] = grade
            mineral_flags[i] = 1 if grade >= cutoff else 0

    return grades, mineral_flags

# =============================================================================
# 5.SURFACE GENERATION - FROM REAL COLLAR DATA
# =============================================================================

def generate_surface(collar_df, padding=50, resolution=40):
    x_min = collar_df['XCOLLAR'].min() - padding
    x_max = collar_df['XCOLLAR'].max() + padding
    y_min = collar_df['YCOLLAR'].min() - padding
    y_max = collar_df['YCOLLAR'].max() + padding

    x_grid = np.linspace(x_min, x_max, resolution)
    y_grid = np.linspace(y_min, y_max, resolution)
    Xs, Ys = np.meshgrid(x_grid, y_grid)

    points = collar_df[['XCOLLAR', 'YCOLLAR']].values
    values = collar_df['ZCOLLAR'].values

    Zs = griddata(points, values, (Xs, Ys), method='linear')

    mask = np.isnan(Zs)
    if mask.any():
        Zs_nearest = griddata(points, values, (Xs, Ys), method='nearest')
        Zs[mask] = Zs_nearest[mask]

    return Xs, Ys, Zs

# =============================================================================
# 6.STRICT ORE-ONLY ALPHA SHAPE
# =============================================================================

def cluster_points_radius(points, eps=120.0, min_pts=4):
    n = len(points)
    if n == 0:
        return np.array([], dtype=int)

    tree = cKDTree(points)
    labels = np.full(n, -1, dtype=int)
    cluster_id = 0

    for i in range(n):
        if labels[i] != -1:
            continue
        neighbors = tree.query_ball_point(points[i], eps)
        if len(neighbors) < min_pts:
            continue
        labels[i] = cluster_id
        queue = list(neighbors)
        while queue:
            j = queue.pop()
            if labels[j] == -1:
                labels[j] = cluster_id
                nbrs = tree.query_ball_point(points[j], eps)
                if len(nbrs) >= min_pts:
                    queue.extend([k for k in nbrs if labels[k] == -1])
        cluster_id += 1

    return labels


def alpha_shape_3d_strict(points, alpha, mineral_tree, barren_tree, barren_margin):
    """
    Create 3D alpha-shape that is STRICTLY within ore zone.Key constraints:
    1.All face vertices must be mineral points
    2.Face centroids must be far from barren points
    3.Faces that extend beyond ore zone are removed
    """
    if len(points) < 4:
        return np.empty((0, 3), dtype=int)

    try:
        tetra = Delaunay(points)
    except Exception as e:
        print(f"    Delaunay failed: {e}")
        return np.empty((0, 3), dtype=int)

    tets = tetra.simplices
    pts_tet = points[tets]

    # Calculate circumradius for each tetrahedron
    radii = np.zeros(len(tets))
    for i, verts in enumerate(pts_tet):
        pa, pb, pc, pd = verts
        A = 2 * np.vstack((pb - pa, pc - pa, pd - pa)).T
        B = np.array([
            np.dot(pb, pb) - np.dot(pa, pa),
            np.dot(pc, pc) - np.dot(pa, pa),
            np.dot(pd, pd) - np.dot(pa, pa),
        ])
        try:
            center = np.linalg.solve(A, B)
            radii[i] = np.linalg.norm(pa - center)
        except:
            radii[i] = np.inf

    # Keep only tetrahedra with circumradius < alpha
    keep = radii < alpha
    tets_kept = tets[keep]

    if tets_kept.size == 0:
        return np.empty((0, 3), dtype=int)

    # Extract boundary faces
    face_count = {}
    def add_face(a, b, c):
        face = tuple(sorted((a, b, c)))
        face_count[face] = face_count.get(face, 0) + 1

    for tet in tets_kept:
        a, b, c, d = tet
        add_face(a, b, c)
        add_face(a, b, d)
        add_face(a, c, d)
        add_face(b, c, d)

    boundary_faces = [list(f) for f, cnt in face_count.items() if cnt == 1]

    if not boundary_faces:
        return np.empty((0, 3), dtype=int)

    faces = np.array(boundary_faces, dtype=int)

    # ===========================================
    # STRICT ORE-ONLY FILTERING
    # ===========================================

    valid_faces = []

    for face in faces:
        # Get face vertices and centroid
        v0, v1, v2 = points[face[0]], points[face[1]], points[face[2]]
        centroid = (v0 + v1 + v2) / 3

        # Also check midpoints of edges
        mid01 = (v0 + v1) / 2
        mid12 = (v1 + v2) / 2
        mid02 = (v0 + v2) / 2

        check_points = [centroid, mid01, mid12, mid02]

        # Check 1: All check points must be close to mineral points
        all_near_mineral = True
        for cp in check_points:
            dist_to_mineral, _ = mineral_tree.query(cp)
            if dist_to_mineral > alpha * 0.8: # Must be within ore zone
                all_near_mineral = False
                break

        if not all_near_mineral:
            continue

        # Check 2: All check points must be far from barren points
        if barren_tree is not None:
            too_close_to_barren = False
            for cp in check_points:
                dist_to_barren, _ = barren_tree.query(cp)
                if dist_to_barren < barren_margin:
                    too_close_to_barren = True
                    break

            if too_close_to_barren:
                continue

        # Check 3: Face normal should not point towards barren zone
        # (This ensures faces wrap around ore, not extend into waste)
        edge1 = v1 - v0
        edge2 = v2 - v0
        normal = np.cross(edge1, edge2)
        normal = normal / (np.linalg.norm(normal) + 1e-10)

        # Check point slightly outside face
        outside_point = centroid + normal * 10

        # This point should not be closer to barren than to mineral
        if barren_tree is not None:
            dist_outside_to_barren, _ = barren_tree.query(outside_point)
            dist_outside_to_mineral, _ = mineral_tree.query(outside_point)

            # If outside point is closer to barren, check other direction
            if dist_outside_to_barren < dist_outside_to_mineral:
                # Try opposite direction
                outside_point_alt = centroid - normal * 10
                dist_alt_to_barren, _ = barren_tree.query(outside_point_alt)
                dist_alt_to_mineral, _ = mineral_tree.query(outside_point_alt)

                # If both directions lead to barren, skip this face
                if dist_alt_to_barren < dist_alt_to_mineral:
                    continue

        valid_faces.append(face)

    if not valid_faces:
        return np.empty((0, 3), dtype=int)

    return np.array(valid_faces, dtype=int)


def build_strict_ore_lodes(borehole_data, controls):
    """
    Build inferred lodes that are STRICTLY within ore zones.Key principles:
    1.Only use REAL mineral sample points
    2.Create tight alpha-shape around mineral points
    3.Remove any faces that extend into non-ore zones
    4.Clip faces near barren samples
    """

    alpha = controls.get('alpha', 100.0)
    cluster_eps = controls.get('cluster_eps', 120.0)
    min_cluster_pts = controls.get('min_cluster_pts', 4)
    barren_margin = controls.get('barren_margin', 15.0)

    # Collect MINERAL samples from REAL data only
    mineral_pts_list = []
    barren_pts_list = []

    for bh in borehole_data:
        trace = bh['trace']
        flags = bh['flags']
        grades = bh['grades']

        # Mineral points (above cutoff)
        mineral_mask = flags == 1
        if mineral_mask.any():
            mineral_pts_list.append(trace[mineral_mask, :3])

        # Barren points (has assay but below cutoff)
        barren_mask = (grades > 0) & (flags == 0)
        if barren_mask.any():
            barren_pts_list.append(trace[barren_mask, :3])

        # Also consider points with no assay as potential barren zones
        # (areas where we drilled but found nothing)
        no_assay_mask = grades == 0
        if no_assay_mask.any():
            # Sample some of these points
            no_assay_pts = trace[no_assay_mask, :3]
            if len(no_assay_pts) > 5:
                # Take every 5th point to avoid too many
                barren_pts_list.append(no_assay_pts[::5])

    if not mineral_pts_list:
        raise RuntimeError("No mineral samples found in REAL data!")

    mineral_pts = np.concatenate(mineral_pts_list, axis=0)
    mineral_tree = cKDTree(mineral_pts)
    print(f"  REAL mineral points: {len(mineral_pts)}")

    barren_tree = None
    if barren_pts_list:
        barren_pts = np.concatenate(barren_pts_list, axis=0)
        barren_tree = cKDTree(barren_pts)
        print(f"  REAL barren/no-assay points: {len(barren_pts)}")

    # Cluster mineral points
    labels = cluster_points_radius(mineral_pts, eps=cluster_eps, min_pts=min_cluster_pts)
    cluster_ids = [cid for cid in np.unique(labels) if cid >= 0]
    print(f"  Ore clusters identified: {len(cluster_ids)}")

    lodes = []

    for cid in cluster_ids:
        idx_cluster = np.where(labels == cid)[0]
        pts_cluster = mineral_pts[idx_cluster]

        if pts_cluster.shape[0] < 4:
            continue

        print(f"    Processing cluster {cid}: {len(pts_cluster)} points")

        # Build cluster-specific trees
        cluster_tree = cKDTree(pts_cluster)

        # Create STRICT ore-only alpha-shape
        faces = alpha_shape_3d_strict(
            pts_cluster,
            alpha=alpha,
            mineral_tree=cluster_tree,
            barren_tree=barren_tree,
            barren_margin=barren_margin
       )

        if faces.size == 0:
            # Try with slightly larger alpha
            print(f"      Retrying with larger alpha...")
            faces = alpha_shape_3d_strict(
                pts_cluster,
                alpha=alpha * 1.3,
                mineral_tree=cluster_tree,
                barren_tree=barren_tree,
                barren_margin=barren_margin
           )

        if faces.size == 0:
            # Last resort: tight convex hull with clipping
            print(f"      Using clipped convex hull...")
            try:
                hull = ConvexHull(pts_cluster)
                faces = hull.simplices

                # Clip convex hull faces near barren
                if barren_tree is not None:
                    valid_faces = []
                    for face in faces:
                        centroid = pts_cluster[face].mean(axis=0)
                        dist_to_barren, _ = barren_tree.query(centroid)
                        if dist_to_barren >= barren_margin:
                            valid_faces.append(face)

                    if valid_faces:
                        faces = np.array(valid_faces)
                    else:
                        continue
            except:
                continue

        if faces.size == 0:
            continue

        print(f"      Final faces: {len(faces)}")

        lodes.append({
            "points": pts_cluster,
            "faces": faces,
            "cluster_id": cid
        })

    # If no clusters formed, try with all mineral points
    if not lodes and len(mineral_pts) >= 4:
        print("  No clusters - using all mineral points as single lode...")

        faces = alpha_shape_3d_strict(
            mineral_pts,
            alpha=alpha * 1.5,
            mineral_tree=mineral_tree,
            barren_tree=barren_tree,
            barren_margin=barren_margin
       )

        if faces.size == 0:
            try:
                hull = ConvexHull(mineral_pts)
                faces = hull.simplices

                # Clip
                if barren_tree is not None:
                    valid_faces = []
                    for face in faces:
                        centroid = mineral_pts[face].mean(axis=0)
                        dist_to_barren, _ = barren_tree.query(centroid)
                        if dist_to_barren >= barren_margin:
                            valid_faces.append(face)
                    if valid_faces:
                        faces = np.array(valid_faces)
            except:
                pass

        if faces.size > 0:
            lodes.append({
                "points": mineral_pts,
                "faces": faces,
                "cluster_id": 0
            })

    return lodes

# =============================================================================
# 7.MAIN VISUALIZATION
# =============================================================================

def create_plot(collar_file, survey_file, assay_file, controls):

    print("=" * 70)
    print("LOADING 100% REAL DATA")
    print("=" * 70)

    collar_df = load_collar_data(collar_file)
    survey_df = load_survey_data(survey_file)
    assay_df = load_assay_data(assay_file)

    cutoff = controls.get('cutoff_grade', 0.2)
    print(f"\nCutoff grade: {cutoff}% Cu")

    print("\nGenerating surface from REAL collar elevations...")
    Xs, Ys, Zs = generate_surface(collar_df,
                                   controls.get('surface_padding', 50),
                                   controls.get('mesh_resolution', 40))

    print("\nProcessing boreholes with REAL survey and assay data...")

    borehole_data = []
    all_mineral_points = []

    holes_with_mineral = 0
    total_mineral_intervals = 0

    for _, row in collar_df.iterrows():
        bhid = row['BHID']
        max_depth = row['DEPTH']

        trace = desurvey_borehole(row, survey_df, max_depth,
                                   controls.get('samples_per_meter', 0.5))

        grades, flags = assign_grades_to_trace(trace, bhid, assay_df, cutoff)

        borehole_data.append({
            'bhid': bhid,
            'trace': trace,
            'grades': grades,
            'flags': flags
        })

        mineral_mask = flags == 1
        if mineral_mask.any():
            all_mineral_points.append(trace[mineral_mask, :3])
            holes_with_mineral += 1
            total_mineral_intervals += mineral_mask.sum()

    if not all_mineral_points:
        raise ValueError(f"No mineral intersections found with cutoff {cutoff}%!")

    mineral_points = np.vstack(all_mineral_points)

    print(f"\n  Boreholes with mineralization: {holes_with_mineral}/{len(collar_df)}")
    print(f"  Total REAL mineral sample points: {len(mineral_points)}")

    print("\nBuilding TRUE orebody (convex hull of REAL mineral points)...")
    try:
        true_hull_pts = mineral_points + np.random.normal(0, 0.1, mineral_points.shape)
        true_hull = ConvexHull(true_hull_pts)
        has_true_hull = True
        print(f"  True hull: {len(true_hull.simplices)} faces")
    except Exception as e:
        print(f"  Could not build true hull: {e}")
        has_true_hull = False
        true_hull_pts = mineral_points

    print("\nBuilding INFERRED lodes (STRICT ORE-ZONE ONLY)...")
    lodes = build_strict_ore_lodes(borehole_data, controls)
    print(f"  Total lodes created: {len(lodes)}")

    if len(mineral_points) > 10:
        pca = PCA(n_components=3)
        pca.fit(mineral_points - mineral_points.mean(axis=0))
        normal = pca.components_[2]
        dip = np.degrees(np.arctan2(np.sqrt(normal[0]**2 + normal[1]**2), abs(normal[2])))
    else:
        dip = 0

    print("\n" + "=" * 70)
    print("CREATING VISUALIZATION")
    print("=" * 70)

    fig = go.Figure()

    # --- 1.SURFACE ---
    fig.add_trace(go.Surface(
        x=Xs, y=Ys, z=Zs,
        colorscale='Earth',
        opacity=0.5,
        showscale=False,
        name='Topography'
   ))

    # --- 2.TRUE OREBODY (GREEN) ---
    if has_true_hull:
        fig.add_trace(go.Mesh3d(
            x=true_hull_pts[:, 0],
            y=true_hull_pts[:, 1],
            z=true_hull_pts[:, 2],
            i=true_hull.simplices[:, 0],
            j=true_hull.simplices[:, 1],
            k=true_hull.simplices[:, 2],
            color="#008000",
            opacity=0.35,
            flatshading=True,
            name="True orebody",
            lighting=dict(ambient=0.6, diffuse=0.8),
       ))
    idx_true = len(fig.data) - 1

    # --- 3.INFERRED LODES (ORANGE) ---
    lode_colors = ["#ff9900", "#ff6600", "#ffcc00", "#ff3300", "#ff0066"]
    lode_indices = []

    for lid, lode in enumerate(lodes):
        pts = lode["points"]
        faces = lode["faces"]
        col = lode_colors[lid % len(lode_colors)]

        fig.add_trace(go.Mesh3d(
            x=pts[:, 0],
            y=pts[:, 1],
            z=pts[:, 2],
            i=faces[:, 0],
            j=faces[:, 1],
            k=faces[:, 2],
            color=col,
            opacity=0.8,
            flatshading=True,
            name=f"Inferred lode {lid+1}",
            lighting=dict(ambient=0.7, diffuse=0.9, specular=0.3),
       ))
        lode_indices.append(len(fig.data) - 1)

    # --- 4.BOREHOLES ---
    first_mineral = True
    first_barren = True

    for bh in borehole_data:
        bhid = bh['bhid']
        trace = bh['trace']
        flags = bh['flags']

        x_line = trace[:, 0]
        y_line = trace[:, 1]
        z_line = trace[:, 2]

        x_min, y_min, z_min = [], [], []
        x_bar, y_bar, z_bar = [], [], []

        for k in range(len(trace)):
            if flags[k] == 1:
                x_min.append(x_line[k])
                y_min.append(y_line[k])
                z_min.append(z_line[k])
                x_bar.append(np.nan)
                y_bar.append(np.nan)
                z_bar.append(np.nan)
            else:
                x_bar.append(x_line[k])
                y_bar.append(y_line[k])
                z_bar.append(z_line[k])
                x_min.append(np.nan)
                y_min.append(np.nan)
                z_min.append(np.nan)

        # Barren (grey)
        fig.add_trace(go.Scatter3d(
            x=x_bar, y=y_bar, z=z_bar,
            mode="lines",
            line=dict(width=4, color="#555555"),
            name="BH (no mineral)" if first_barren else "",
            showlegend=first_barren,
            legendgroup="boreholes",
            hovertext=bhid,
            hoverinfo='text'
       ))
        first_barren = False

        # Mineral (green)
        if any(f == 1 for f in flags):
            fig.add_trace(go.Scatter3d(
                x=x_min, y=y_min, z=z_min,
                mode="lines",
                line=dict(width=4, color="#00aa00"),
                name="BH (mineral)" if first_mineral else "",
                showlegend=first_mineral,
                legendgroup="boreholes",
                hovertext=bhid,
                hoverinfo='text'
           ))
            first_mineral = False

    # --- 5.BOREHOLE COLLARS ---
    collars = np.array([bh['trace'][0, :3] for bh in borehole_data])
    fig.add_trace(go.Scatter3d(
        x=collars[:, 0],
        y=collars[:, 1],
        z=collars[:, 2],
        mode="markers",
        marker=dict(size=6, symbol="circle", color="black"),
        name="Borehole collars",
        legendgroup="boreholes"
   ))

    # --- 6.BH INTERSECTIONS ---
    inter_pts = []
    for bh in borehole_data:
        trace = bh['trace']
        flags = bh['flags']
        mineral_indices = np.where(flags == 1)[0]
        if len(mineral_indices) > 0:
            inter_pts.append(trace[mineral_indices[0], :3])
            if len(mineral_indices) > 2:
                inter_pts.append(trace[mineral_indices[-1], :3])

    if inter_pts:
        inter_pts = np.array(inter_pts)
        fig.add_trace(go.Scatter3d(
            x=inter_pts[:, 0],
            y=inter_pts[:, 1],
            z=inter_pts[:, 2],
            mode="markers",
            marker=dict(size=6, symbol="diamond", color="#008000"),
            name="BH intersections",
            legendgroup="boreholes"
       ))

    # --- VISIBILITY TOGGLES ---
    n_traces = len(fig.data)
    vis_all = [True] * n_traces

    vis_true_only = [True] * n_traces
    for li in lode_indices:
        vis_true_only[li] = False

    vis_inferred_only = [True] * n_traces
    vis_inferred_only[idx_true] = False

    vis_no_ore = [True] * n_traces
    vis_no_ore[idx_true] = False
    for li in lode_indices:
        vis_no_ore[li] = False

    # --- LAYOUT ---
    fig.update_layout(
        title=dict(
            text=(f"<b>True vs Inferred Orebody - 100% REAL DATA</b><br>"
                  f"<sup>Dip: {dip:.0f}, Cutoff: {cutoff}% Cu, "
                  f"Mineral Points: {len(mineral_points)} (STRICT ORE-ZONE ONLY)</sup>"),
            x=0.5,
            font=dict(size=16)
       ),
        scene=dict(
            xaxis_title="Easting (X)",
            yaxis_title="Northing (Y)",
            zaxis_title="Elevation (Z)",
            aspectmode='data',
            camera=dict(
                eye=dict(x=1.6, y=1.6, z=1.0),
                up=dict(x=0, y=0, z=1)
           ),
            bgcolor='rgb(245, 245, 250)'
       ),
        legend=dict(
            x=0.82, y=0.98,
            bgcolor='rgba(255,255,255,0.9)',
            bordercolor='black', borderwidth=1
       ),
        margin=dict(l=0, r=0, t=80, b=0),

        updatemenus=[dict(
            type="buttons", direction="right",
            x=0.02, y=1.12,
            buttons=[
                dict(label="Both (true + inferred)",
                     method="update", args=[{"visible": vis_all}]),
                dict(label="True only",
                     method="update", args=[{"visible": vis_true_only}]),
                dict(label="Inferred only",
                     method="update", args=[{"visible": vis_inferred_only}]),
                dict(label="No orebody (data only)",
                     method="update", args=[{"visible": vis_no_ore}]),
            ]
       )]
   )

    fig.show()

    print("\n" + "=" * 70)
    print("SUMMARY - 100% REAL DATA, STRICT ORE-ZONE ONLY")
    print("=" * 70)
    print(f"\nData sources (ALL REAL):")
    print(f"  Collars: {collar_file}")
    print(f"  Surveys: {survey_file}")
    print(f"  Assays: {assay_file}")
    print(f"\nResults:")
    print(f"  Total boreholes: {len(collar_df)}")
    print(f"  Boreholes with ore: {holes_with_mineral}")
    print(f"  Mineral sample points: {len(mineral_points)}")
    print(f"  Inferred lodes: {len(lodes)}")
    for i, lode in enumerate(lodes):
        print(f"    Lode {i+1}: {len(lode['points'])} points, {len(lode['faces'])} faces")

    return fig, lodes


# =============================================================================
# RUN
# =============================================================================

if __name__ == "__main__":

    COLLAR_FILE = "Combined_Collar.csv"
    SURVEY_FILE = "Combined_Survey.csv"
    ASSAY_FILE = "COMBINED_ASSAY_WITH_MHCM.csv"

    fig, lodes = create_plot(
        COLLAR_FILE,
        SURVEY_FILE,
        ASSAY_FILE,
        CONTROLS
   )

    fig.write_html("ore_STRICT_ORE_ONLY_real_data.html")
    print("\nSaved to: ore_STRICT_ORE_ONLY_real_data.html")
